In [3]:
# Install Java, Spark, and Findspark
!apt-get update
# Install Java, Spark, and Findspark
!apt-get install openjdk-8-jdk-headless -qq > /dev/null
!wget -q https://downloads.apache.org/spark/spark-3.0.0/spark-3.0.0-bin-hadoop2.7.tgz
!tar xf spark-3.0.0-bin-hadoop2.7.tgz
!pip install -q findspark


# Set Environment Variables
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = "/content/spark-3.0.0-bin-hadoop2.7"

# Start a SparkSession
import findspark
findspark.init()

Hit:1 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran35/ InRelease
Ign:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Ign:3 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Hit:4 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release
Hit:5 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  Release
Hit:6 http://archive.ubuntu.com/ubuntu bionic InRelease
Hit:7 http://security.ubuntu.com/ubuntu bionic-security InRelease
Hit:8 http://ppa.launchpad.net/graphics-drivers/ppa/ubuntu bionic InRelease
Hit:9 http://archive.ubuntu.com/ubuntu bionic-updates InRelease
Hit:11 http://archive.ubuntu.com/ubuntu bionic-backports InRelease
Hit:12 http://ppa.launchpad.net/marutter/c2d4u3.5/ubuntu bionic InRelease
Reading package lists... Done


In [1]:
# !pip install stanfordnlp
# import stanfordnlp
# stanfordnlp.download('en')   # This downloads the English models for the neural pipeline
# nlp = stanfordnlp.Pipeline() # This sets up a default neural pipeline in English
# doc = nlp("Barack Obama was born in Hawaii.  He was elected president in 2008.")
# doc.sentences[0].print_dependencies()

In [4]:
# Start Spark session
from pyspark.sql import SparkSession
spark = SparkSession.builder.appName("NaiveBayes") \
    .config("spark.driver.memory", "50g") \
    .appName('my-cool-app') \
    .getOrCreate()
# .master('local[*]') \

In [5]:
from google.colab import files
data = files.upload()

Saving genre_lyrics_data.csv to genre_lyrics_data.csv


In [ ]:
data

{'genre_lyrics.csv': b',genre_name,lyrics\n0,acoustic,"well, you done done me and you bet i felt it, i tried to be chill, but you\'re so hot that i melted, i fell right through the cracks, now i\'m trying to get back, before the cool done run out, i\'ll be giving it my bestest, and nothing\'s gonna stop me but divine intervention. i reckon, it\'s again my turn, to win some or learn some. but i won\'t hesitate, no more, no more. it cannot wait, i\'m yours. well, open up your mind and see like me, open up your plans and damn you\'re free. look into your heart and you\'ll find love, love, love, love. listen to the music of the moment, people dance and sing, we\'re just one big family, and it\'s our god-forsaken right to be loved, loved, loved, loved, loved, so i won\'t hesitate, no more, no more. it cannot wait, i\'m sure. there\'s no need to complicate. our time is short. this is our fate, i\'m yours. do you want to come on, scooch on over closer, dear, and i will nibble your ear, i\'ve 

In [6]:
# from pyspark import SparkFiles
# spark.sparkContext.addFile(url)
df = spark.read.csv("genre_lyrics_data.csv", sep=",", header=True)
df = df.select('genre_name','lyrics_cleaned')
# Show DataFrame
df.show()

+----------+--------------------+
|genre_name|      lyrics_cleaned|
+----------+--------------------+
|  acoustic|well you done don...|
|  acoustic|head under water ...|
|  acoustic|will you count me...|
|  acoustic|do you hear me im...|
|  acoustic|the strands in yo...|
|  acoustic|when im out walki...|
|  acoustic|something always ...|
|  acoustic|its not simple to...|
|  acoustic|2 am and she call...|
|  acoustic|2 am and she call...|
|  acoustic|wanna lie to you ...|
|  acoustic|the dawn is break...|
|  acoustic|in the light of t...|
|  acoustic|when you came to ...|
|  acoustic|baby lets stay ho...|
|  acoustic|may you have ausp...|
|  acoustic|ive got the dynam...|
|  acoustic|ive got the dynam...|
|  acoustic|im taking a momen...|
|  acoustic|well i have been ...|
+----------+--------------------+
only showing top 20 rows



In [7]:
from pyspark.sql.functions import length
# Create a length column to be used as a future feature 
data_df = df.withColumn('length', length(df['lyrics_cleaned']))
data_df.show()

+----------+--------------------+------+
|genre_name|      lyrics_cleaned|length|
+----------+--------------------+------+
|  acoustic|well you done don...|  1649|
|  acoustic|head under water ...|  1882|
|  acoustic|will you count me...|  1372|
|  acoustic|do you hear me im...|  1306|
|  acoustic|the strands in yo...|  1306|
|  acoustic|when im out walki...|   922|
|  acoustic|something always ...|  1085|
|  acoustic|its not simple to...|  1368|
|  acoustic|2 am and she call...|    84|
|  acoustic|2 am and she call...|    84|
|  acoustic|wanna lie to you ...|  1572|
|  acoustic|the dawn is break...|   855|
|  acoustic|in the light of t...|  1149|
|  acoustic|when you came to ...|   895|
|  acoustic|baby lets stay ho...|  1110|
|  acoustic|may you have ausp...|   238|
|  acoustic|ive got the dynam...|  2794|
|  acoustic|ive got the dynam...|  2794|
|  acoustic|im taking a momen...|  2433|
|  acoustic|well i have been ...|  1080|
+----------+--------------------+------+
only showing top

In [8]:
from pyspark.ml.feature import Tokenizer, StopWordsRemover, HashingTF, IDF, StringIndexer
# Create all the features to the data set
pos_neg_to_num = StringIndexer(inputCol='genre_name',outputCol='label')
tokenizer = Tokenizer(inputCol="lyrics_cleaned", outputCol="token_text")
stopremove = StopWordsRemover(inputCol='token_text',outputCol='stop_tokens')
hashingTF = HashingTF(inputCol="stop_tokens", outputCol='hash_token')
idf = IDF(inputCol='hash_token', outputCol='idf_token')


In [9]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.linalg import Vector

# Create feature vectors
clean_up = VectorAssembler(inputCols=['idf_token', 'length'], outputCol='features')

In [10]:
# Create a and run a data processing Pipeline
from pyspark.ml import Pipeline
data_prep_pipeline = Pipeline(stages=[pos_neg_to_num, tokenizer, stopremove, hashingTF, idf, clean_up])

In [11]:
# Fit and transform the pipeline
cleaner = data_prep_pipeline.fit(data_df)
cleaned = cleaner.transform(data_df)

In [12]:
# Show label and resulting features
cleaned.select(['label', 'features']).show()

+-----+--------------------+
|label|            features|
+-----+--------------------+
|  3.0|(262145,[8538,958...|
|  3.0|(262145,[1797,243...|
|  3.0|(262145,[5765,723...|
|  3.0|(262145,[2437,576...|
|  3.0|(262145,[8449,112...|
|  3.0|(262145,[14072,17...|
|  3.0|(262145,[4372,576...|
|  3.0|(262145,[991,2437...|
|  3.0|(262145,[12524,17...|
|  3.0|(262145,[12524,17...|
|  3.0|(262145,[991,3924...|
|  3.0|(262145,[7625,853...|
|  3.0|(262145,[6261,844...|
|  3.0|(262145,[5765,844...|
|  3.0|(262145,[8538,133...|
|  3.0|(262145,[3436,215...|
|  3.0|(262145,[619,706,...|
|  3.0|(262145,[619,706,...|
|  3.0|(262145,[3186,392...|
|  3.0|(262145,[2751,419...|
+-----+--------------------+
only showing top 20 rows



In [13]:
from pyspark.ml.classification import NaiveBayes, NaiveBayesModel
# Break data down into a training set and a testing set
training, testing = cleaned.randomSplit([0.7, 0.3])

# Create a Naive Bayes model and fit training data
nb = NaiveBayes()
predictor = nb.fit(training)

In [14]:
# import pickle
# pickle.dump(nb, open('model.pkl','wb'))
predictor.save("lyric_model")

In [15]:
model = NaiveBayesModel.load("lyric_model")

In [19]:
testing.show(5)

+----------+--------------------+------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+
|genre_name|      lyrics_cleaned|length|label|          token_text|         stop_tokens|          hash_token|           idf_token|            features|
+----------+--------------------+------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+
|  acoustic|2 am and she call...|    84|  3.0|[2, am, and, she,...|[2, calls, cause,...|(262144,[12524,17...|(262144,[12524,17...|(262145,[12524,17...|
|  acoustic|3 am shell call y...|  1571|  3.0|[3, am, shell, ca...|[3, shell, call, ...|(262144,[2325,576...|(262144,[2325,576...|(262145,[2325,576...|
|  acoustic|all of these line...|  1031|  3.0|[all, of, these, ...|[lines, across, f...|(262144,[535,6769...|(262144,[535,6769...|(262145,[535,6769...|
|  acoustic|and i will hold y...|   992|  3.0|[and, i, will, ho...|[hold, tight, lik...|

In [20]:
# Tranform the model with the testing data
test_results = model.transform(testing)
test_results.show(5)

+----------+--------------------+------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+----------+
|genre_name|      lyrics_cleaned|length|label|          token_text|         stop_tokens|          hash_token|           idf_token|            features|       rawPrediction|         probability|prediction|
+----------+--------------------+------+-----+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+----------+
|  acoustic|2 am and she call...|    84|  3.0|[2, am, and, she,...|[2, calls, cause,...|(262144,[12524,17...|(262144,[12524,17...|(262145,[12524,17...|[-497.91580528233...|[2.12472415534835...|       3.0|
|  acoustic|3 am shell call y...|  1571|  3.0|[3, am, shell, ca...|[3, shell, call, ...|(262144,[2325,576...|(262144,[2325,576...|(262145,[2325,576...|[-5760.8266495784...|[1.0,2.1

In [21]:
# # Tranform the model with the testing data
# test_results = predictor.transform(testing)
# test_results.show(5)

In [22]:
# Use the Class Evaluator for a cleaner description
from pyspark.ml.evaluation import MulticlassClassificationEvaluator

acc_eval = MulticlassClassificationEvaluator()
acc = acc_eval.evaluate(test_results)
print("Accuracy of model at predicting reviews was: %f" % acc)

Accuracy of model at predicting reviews was: 0.064381
